# Linear Convex Optimization with Gurobi

## Example 1: Furniture Factory

In [ ]:
import gurobipy as gp
from gurobipy import GRB

In [ ]:
# Create a new model
m = gp.Model('factory')

In [ ]:
# Create variables
x1 = m.addVar(name='chairs')
x2 = m.addVar(name='tables')

In [ ]:
# Set the objective
m.setObjective(45*x1 + 80*x2, GRB.MAXIMIZE)

In [ ]:
# Add constraints
m.addConstr(5*x1 + 20*x2 <= 400, 'mahogany');
m.addConstr(10*x1 + 15*x2 <= 450, 'labor');
m.addConstr(x1 >= 0, 'non_neg1');
m.addConstr(x2 >= 0, 'non_neg2');

In [ ]:
m.optimize()

In [ ]:
# Display solution
for v in m.getVars():
    print(f'{v.varName} --> {v.x}')
print(f'Optimal total revenue: {m.objVal}')

What if we want to be sure to have integer variables?

In [ ]:
m = gp.Model('factory')
x1 = m.addVar(name='chairs', vtype=GRB.INTEGER)
x2 = m.addVar(name='tables', vtype=GRB.INTEGER)
m.setObjective(45*x1 + 80*x2, GRB.MAXIMIZE)
m.addConstr(5*x1 + 20*x2 <= 400, 'mahogany')
m.addConstr(10*x1 + 15*x2 <= 450, 'labor')
m.addConstr(x1 >= 0, 'non_neg1')
m.addConstr(x2 >= 0, 'non_neg2')
m.optimize()

for v in m.getVars():
    print(f'{v.varName} --> {v.x}')
print(f'Optimal total revenue: {m.objVal}')

Notice the different output (for the same result).

## Example 2: Knapsack Problem

Often formulate a problem in terms of Linear Programming is not the most efficient way to solve it. However, this approach is very flexible.   
As an example, we start from formulating the Knapsack Problem as an LP instance (https://github.com/mathcoding/opt4ds)

In [ ]:
m = gp.Model('knapsack')

goods, values = gp.multidict({
    'necklace':2,
    'laptop':3,
    'phone':1,
    'ring':4,
    'clock':3
})

weights = {
    'necklace':3,
    'laptop':4,
    'phone':2,
    'ring':1,
    'clock':6
}

capacity = 9

Add the decision variables:

In [ ]:
take = m.addVars(goods, name="take", vtype=GRB.BINARY)

Set the objective and the capacity constraint

In [ ]:
m.setObjective(take.prod(values), GRB.MAXIMIZE)
# m.setObjective(sum(take[f]*values[f] for f in goods), GRB.MAXIMIZE)

m.addConstr((gp.quicksum(weights[f] * take[f] for f in goods) <= capacity))

Solve the model:

In [ ]:
m.optimize()

In [ ]:
def printSol():
    if m.status == GRB.OPTIMAL:
        print(f'Knapsack Value: {m.ObjVal}')
        print('Take: ',end='')
        for g in goods:
            if take[g].x > 0.001:
                print(f'{g}; ', end='')
        print(f'\nCapacity: {sum(weights[f] * take[f].x for f in goods)}/{capacity}')
printSol()

## Example 3: Sudoku (Feasibility problem)

Also the Sudoku can be solved as an MIP instance.   
Read the instance:

In [ ]:
grid = open('sudoku_instance').read().split()
for i in grid:
    print(i)

n = 9 # grid size
s = 3 # sub-square size

In [ ]:
model = gp.Model('sudoku')

vars = model.addVars(n, n, n, vtype=GRB.BINARY, name='G')

In [ ]:
# Fix variables associated with cells whose values are pre-specified

for i in range(n):
    for j in range(n):
        if grid[i][j] != '.':
            v = int(grid[i][j]) - 1
            vars[i, j, v].LB = 1


In [ ]:
# Each cell must take one value

model.addConstrs(
    (vars.sum(i, j, '*') == 1
    for i in range(n)
    for j in range(n)), name='V');

In [ ]:
# Each value appears once per row

model.addConstrs(
    (vars.sum(i, '*', v) == 1
    for i in range(n)
    for v in range(n)), name='R');

In [ ]:
# Each value appears once per column

model.addConstrs(
    (vars.sum('*', j, v) == 1
    for j in range(n)
    for v in range(n)), name='C');

In [ ]:
# Each value appears once per subgrid

model.addConstrs((
    gp.quicksum(vars[i, j, v] for i in range(i0*s, (i0+1)*s)
                for j in range(j0*s, (j0+1)*s)) == 1
    for v in range(n)
    for i0 in range(s)
    for j0 in range(s)), name='Sub');


In [ ]:
model.optimize() # No objective!!

In [ ]:
solution = model.getAttr('X', vars)

for i in range(n):
    sol = ''
    for j in range(n):
        for v in range(n):
            if solution[i, j, v] > 0.5:
                sol += str(v+1)
    print(sol)

**Similar problems:**

- Sudoku with additional constraints
- Magic squares
- n-queens problem

## More examples

- TSP (subtour elimination)
- TSP generalization (CVRP)
- Generic graph problems (shortest path, network flow...)
- Optimal transport
- Scheduling
- Linear classification
- ...